In [ ]:
!pip install datasets

INFO: pip is looking at multiple versions of multiprocess to determine which version is compatible with other requirements. This could take a while.
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 471.6/471.6 kB 32.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 10.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 13.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 19.4 MB/s eta 0:00:00


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
%cd /content/drive/MyDrive/LLM_proje/bert

/content/drive/MyDrive/LLM_proje/bert


In [16]:
import pandas as pd
from sklearn.preprocessing import LabelEncoder
from datasets import Dataset
import numpy as np

# Read the train, test, and eval CSV files
train_df = pd.read_csv('./data_splitted/train.csv', delimiter="\t")
test_df =  pd.read_csv('./data_splitted/val.csv', delimiter="\t")
eval_df = pd.read_csv('./data_splitted/test.csv', delimiter="\t")

# If your CSV files don't have headers, you can set them like this
train_df.columns = ['category', 'ner_tags', 'text']
test_df.columns = ['category', 'ner_tags', 'text']
eval_df.columns = ['category', 'ner_tags', 'text']

le = LabelEncoder()
train_df['label'] = le.fit_transform(train_df['category'])
test_df['label'] = le.transform(test_df['category'])  # Transform test data using the same encoder
eval_df['label'] = le.transform(eval_df['category'])  # Transform eval data using the same encoder

label_mapping = dict(enumerate(le.classes_))

# Combine NER tags from all datasets to get all unique tags
unique_ner_tags = set(
    tag
    for tags in pd.concat([train_df['ner_tags'], test_df['ner_tags'], eval_df['ner_tags']])
    for tag in tags.split()
)
unique_ner_tags.discard('O')  # Remove the 'O' tag if it's present

# Create special tokens for each unique NER tag
special_tokens = {tag: f"[{tag.upper()}_START]" for tag in unique_ner_tags}

# Add continuation tokens for tags that start with 'B-'
for tag in unique_ner_tags:
    if tag.startswith('B-'):
        i_tag = tag.replace('B-', 'I-')
        special_tokens[i_tag] = f"[{i_tag.upper()}_CONT]"

# Define a function to annotate the text with special tokens
def annotate_text(row):
    words = row['text'].split()
    tags = row['ner_tags'].split()
    annotated_text = []
    for word, tag in zip(words, tags):
        if tag != 'O':
            # Add special tokens before and after the entity
            annotated_word = f"{special_tokens[tag]} {word} {special_tokens[tag]}"
            annotated_text.append(annotated_word)
        else:
            annotated_text.append(word)
    return ' '.join(annotated_text)

# Apply the annotation function to all datasets
train_df['annotated_text'] = train_df.apply(annotate_text, axis=1)
test_df['annotated_text'] = test_df.apply(annotate_text, axis=1)
eval_df['annotated_text'] = eval_df.apply(annotate_text, axis=1)

# Convert the pandas DataFrames to Hugging Face Datasets
train_dataset = Dataset.from_pandas(train_df)
test_dataset = Dataset.from_pandas(test_df)
eval_dataset = Dataset.from_pandas(eval_df)

# Create a dictionary to hold all three datasets
ds = {"train": train_dataset, "test": test_dataset, "eval": eval_dataset}

# Display the column names of the training dataset
print(ds["train"].column_names)


['category', 'ner_tags', 'text', 'label', 'annotated_text']


In [ ]:
import os
import pandas as pd
from transformers import BertTokenizer
from transformers import TFBertForSequenceClassification, BertConfig
import torch
#import torchvision.datasets as datasets
#import torchvision.transforms as transforms
import numpy as np
from transformers import DataCollatorWithPadding, Trainer, TrainingArguments, AutoTokenizer, AutoModelForSequenceClassification
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
from sklearn.utils.class_weight import compute_class_weight
from sklearn.model_selection import train_test_split

from torch import nn
from transformers import DataCollatorWithPadding, EarlyStoppingCallback
from datasets import Dataset
from sklearn.preprocessing import LabelEncoder
from sklearn.utils.class_weight import compute_class_weight


if torch.cuda.is_available():
    device = torch.device("cuda")
else:
    device = torch.device("cpu")

print(f"Using device: {device}")

Using device: cuda


In [ ]:
#Annotate Text with Special Tokens: simple, allows the model to recognize entities
# through special tokens.
#Concatenate NER Embeddings: Provides a deeper integration by combining
# NER embeddings with token embeddings. need to modify model to take additional embedding

In [ ]:
splits = ["train", "test"]

df = pd.read_csv('TWNERTC_TC_Fine Grained NER_DomainIndependent_NoiseReduction.DUMP', sep='\t', encoding='utf-8',header=None)

df.columns = ['category', 'ner_tags', 'text']

le = LabelEncoder()
df['label'] = le.fit_transform(df['category'])

label_mapping = dict(enumerate(le.classes_))

#smaller set
#df = df.sample(n=5000)
_, df = train_test_split(df, test_size=8000/len(df),random_state=42, stratify=df['label'])

In [ ]:
unique_ner_tags = set(tag for tags in df['ner_tags'] for tag in tags.split())
unique_ner_tags.discard('O')

special_tokens = {tag: f"[{tag.upper()}_START]" for tag in unique_ner_tags}

for tag in unique_ner_tags:
    if tag.startswith('B-'):
        i_tag = tag.replace('B-', 'I-')
        special_tokens[i_tag] = f"[{i_tag.upper()}_CONT]"

print("Special Tokens:", special_tokens)

Special Tokens: {'I-football_league_name': '[I-FOOTBALL_LEAGUE_NAME_CONT]', 'B-fictional_character_name': '[B-FICTIONAL_CHARACTER_NAME_START]', 'B-tv_program_actor': '[B-TV_PROGRAM_ACTOR_START]', 'I-country_administrative_divisions': '[I-COUNTRY_ADMINISTRATIVE_DIVISIONS_CONT]', 'B-family_member_name': '[B-FAMILY_MEMBER_NAME_START]', 'B-month_calendar_system': '[B-MONTH_CALENDAR_SYSTEM_START]', 'B-programming_language_paradigm_name': '[B-PROGRAMMING_LANGUAGE_PARADIGM_NAME_START]', 'B-dimension_name': '[B-DIMENSION_NAME_START]', 'B-tv_character_series': '[B-TV_CHARACTER_SERIES_START]', 'B-moon_name': '[B-MOON_NAME_START]', 'B-project_name': '[B-PROJECT_NAME_START]', 'I-island_island_group': '[I-ISLAND_ISLAND_GROUP_CONT]', 'B-chemical_compound_formula': '[B-CHEMICAL_COMPOUND_FORMULA_START]', 'B-educational_institution_degree': '[B-EDUCATIONAL_INSTITUTION_DEGREE_START]', 'B-chemical_classification_name': '[B-CHEMICAL_CLASSIFICATION_NAME_START]', 'B-disease_causes': '[B-DISEASE_CAUSES_START

In [ ]:
def annotate_text(row):
    words = row['text'].split()
    tags = row['ner_tags'].split()
    annotated_text = []
    for word, tag in zip(words, tags):
        if tag != 'O':
            # Add special token before and after the entity
            annotated_word = f"{special_tokens[tag]} {word} {special_tokens[tag]}"
            annotated_text.append(annotated_word)
        else:
            annotated_text.append(word)
    return ' '.join(annotated_text)
df['annotated_text'] = df.apply(annotate_text, axis=1)
# update tokenized and model

category                                           ner_tags  \
470050                book  O O O O O O B-deceased_person_place_of_death O...   
479179              people  O B-award_nominee_year O O O O O O B-person_na...   
377036              people                          O O B-person_children O O   
143254             biology  B-organism_classification_name I-organism_clas...   
225099               music  B-artist_name I-artist_name O O O O O O O O O ...   
609244            location  O O O O O O B-country_administrative_divisions...   
496856              soccer  O O O O O O O O B-pro_athlete_team B-pro_athle...   
144689            medicine                 B-symptom_name O O O O O O O O O O   
109162              people        O B-pro_athlete_sport O B-person_name O O O   
631441              people  O B-person_name B-composition_form B-film_char...   
114304           education  O O B-academic_institution_to O O O O B-academ...   
171257      transportation  B-satellite_name I-satellite_name O O O O O O ...   
634193                food  O O O O B-food_name O O O O O O O O O O O O O ...   
547559            business  B-brand_name O O B-organization_name I-organiz...   
254985            medicine  O O O O O B-disease_parent_disease O O O O B-d...   
93687             location  B-location_name I-location_name B-person_natio...   
581834                  tv  O B-tv_series_episode_name I-tv_series_episode...   
486845               music                       O O B-artist_album O O O O O   
181615             royalty              O B-monarch_name I-monarch_name O O O   
465253        organization  B-organization_name O O B-person_profession O ...   
5087            government                  B-politician_name O O O O O O O O   
580910        organization  B-organization_name O B-organization_name I-or...   
232262              people                B-profession_name O O O O O O O O O   
233422              people   O O O B-location_containedby O O O O O O O O O O   
452109               music  O O O B-composition_form B-composition_compose...   
149037               award  O O B-country_form_of_government O O O O O O O...   
403401            location  B-citytown_name I-citytown_name I-citytown_nam...   
221872  fictional_universe  B-character_species_name O O O O O O B-media_g...   
155204                book  B-author_name I-author_name O O O O O B-person...   
128588            location  O O O O O B-location_name I-location_name O O ...   
463405              people  O B-album_release_type B-person_name O O O O O...   
419902            military  O O O O O O O O O O O B-military_conflict_loca...   
188530           geography          B-lake_name I-lake_name O O O O O O O O O   
623096                  tv  B-tv_program_network O O B-adaptation_adapted_...   
145389           astronomy  O B-celestial_object_category_name O O O O O O...   
534390           astronomy                B-galaxy_name I-galaxy_name O O O O   
270669               opera  B-opera_name O O O B-opera_name O O O O O O O ...   
493776            location  B-citytown_name B-location_partially_contains ...   
471301          government      O O O B-form_of_government_name O O O O O O O   
527347               games  O O O O O O O O O O O O O O B-film_character O...   
245089              people  B-film_film_festivals B-film_genre O O B-it_re...   
543004            location  O O O O O O O B-protected_site_iucn_category O...   
206218            medicine  O O O O B-anatomical_structure_name O B-anatom...   
264354              people            O O O O O O O O O O B-person_name O O O   
247018           geography  O O O O B-geographical_feature_name O B-cityto...   
159657            location  B-location_containedby O O O B-person_ethnicit...   
292689              people  O O O O O O O B-location_partially_containedby...   
640074            computer      B-software_genre_name O O O O O O O O O O O O   
432995                film         O B-film_genre

In [ ]:
train_df, test_df = train_test_split(df, test_size=0.2, random_state=42,stratify=df['label'] ) # proportion of each class is the same in both sets

train_dataset = Dataset.from_pandas(train_df)
test_dataset = Dataset.from_pandas(test_df)

ds = {"train": train_dataset, "test": test_dataset}

ds["train"].column_names

['category',
 'ner_tags',
 'text',
 'label',
 'annotated_text',
 '__index_level_0__']

In [ ]:
#from transformers, add NER tag tokens
tokenizer = BertTokenizer.from_pretrained('dbmdz/distilbert-base-turkish-cased', do_lower_case=True)
#tokenizer.add_special_tokens({'additional_special_tokens': list(special_tokens.values())})


def preprocess_function(examples):
    inputs = tokenizer(examples['text'], truncation=True, padding='max_length', max_length=512)
    inputs.pop("token_type_ids", None)
    return inputs

splits = ["train", "test"]
tokenized_ds = {}
for split in splits:
    ds[split] = ds[split].remove_columns(['ner_tags','category','annotated_text'])
    tokenized_ds[split] = ds[split].map(preprocess_function, batched=True)
    tokenized_ds[split] = tokenized_ds[split].remove_columns(["text"]) #model can not take str, give error

print(len(set(tokenized_ds["train"]["label"])))
tokenized_ds

The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'DistilBertTokenizer'. 
The class this function is called from is 'BertTokenizer'.
/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


Map:   0%|          | 0/453466 [00:00<?, ? examples/s]

KeyboardInterrupt: 

In [ ]:
#from transformers, add NER tag tokens
tokenizer = BertTokenizer.from_pretrained('dbmdz/distilbert-base-turkish-cased', do_lower_case=True)
#tokenizer.add_special_tokens({'additional_special_tokens': list(special_tokens.values())})
tokenizer.save_pretrained('./saved_tokenizer2')
import json
with open("./saved_tokenizer/added_tokens.json", "r") as file:
      f = json.load(file)
sorted_f = dict(sorted(f.items(), key=lambda item: item[1]))
sorted_f.values()
my_list = list(sorted_f.keys())

with open('./saved_tokenizer/vocab.txt', 'a') as file:
    for item in my_list:
        file.write(item + '\n')


The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'DistilBertTokenizer'. 
The class this function is called from is 'BertTokenizer'.


('./saved_tokenizer2/tokenizer_config.json',
 './saved_tokenizer2/special_tokens_map.json',
 './saved_tokenizer2/vocab.txt',
 './saved_tokenizer2/added_tokens.json')

In [ ]:
tokenizer = BertTokenizer.from_pretrained('./saved_tokenizer2')

In [17]:
def preprocess_function(examples):
    inputs = tokenizer(examples['annotated_text'], truncation=True, padding='max_length', max_length=512)
    inputs.pop("token_type_ids", None)
    return inputs

splits = ["train", "test","eval"]
tokenized_ds = {}
for split in splits:
    ds[split] = ds[split].remove_columns(['ner_tags','category','text'])
    tokenized_ds[split] = ds[split].map(preprocess_function, batched=True)
    tokenized_ds[split] = tokenized_ds[split].remove_columns(["annotated_text"]) #model can not take str, give error

print(len(set(tokenized_ds["train"]["label"])))
tokenized_ds

Map:   0%|          | 0/453466 [00:00<?, ? examples/s]

Map:   0%|          | 0/129562 [00:00<?, ? examples/s]

Map:   0%|          | 0/64781 [00:00<?, ? examples/s]

49


{'train': Dataset({
     features: ['label', 'input_ids', 'attention_mask'],
     num_rows: 453466
 }),
 'test': Dataset({
     features: ['label', 'input_ids', 'attention_mask'],
     num_rows: 129562
 }),
 'eval': Dataset({
     features: ['label', 'input_ids', 'attention_mask'],
     num_rows: 64781
 })}

In [ ]:
print(f"Unique labels: {len(label_mapping)}")
print(f"Label Mapping: {dict(enumerate(label_mapping))}")
print("current label count: ",len(set(tokenized_ds["train"]["label"])))
print("current label count: ",len(set(tokenized_ds["test"]["label"])))

Unique labels: 49
Label Mapping: {0: 0, 1: 1, 2: 2, 3: 3, 4: 4, 5: 5, 6: 6, 7: 7, 8: 8, 9: 9, 10: 10, 11: 11, 12: 12, 13: 13, 14: 14, 15: 15, 16: 16, 17: 17, 18: 18, 19: 19, 20: 20, 21: 21, 22: 22, 23: 23, 24: 24, 25: 25, 26: 26, 27: 27, 28: 28, 29: 29, 30: 30, 31: 31, 32: 32, 33: 33, 34: 34, 35: 35, 36: 36, 37: 37, 38: 38, 39: 39, 40: 40, 41: 41, 42: 42, 43: 43, 44: 44, 45: 45, 46: 46, 47: 47, 48: 48}
current label count:  49
current label count:  49


In [ ]:
from sklearn.metrics import classification_report, confusion_matrix

def print_conf(predictions, labels):
    all_labels = sorted(list(set(predictions).union(set(labels))))
    nested_dict = dict()

    for l in all_labels:
        nested_dict[l] = dict()
        for l2 in all_labels:
            nested_dict[l][l2] = 0

    for l, p in zip(labels, predictions):
        nested_dict[l][p] += 1

    list_version = list()
    for l in all_labels:
        cur_list = list()
        for p in all_labels:
            cur_list.append(nested_dict[l][p])
        list_version.append(cur_list)

    # Convert list version to DataFrame with row and column indices labeled
    conf_matrix_df = pd.DataFrame(list_version, index=all_labels, columns=all_labels)

    # Print the confusion matrix
    print("Confusion Matrix:")
    print(conf_matrix_df)





In [ ]:
from sklearn.metrics import classification_report

def compute_metrics(eval_pred):
    try:
        predictions, labels = eval_pred
        predictions = np.argmax(predictions, axis=1)
        average_type = 'weighted' #macro: each class independently, weighted: giving more weight to classes with more samples

        accuracy = (predictions == labels).mean()
        precision = precision_score(labels, predictions, average=average_type, zero_division=0)
        recall = recall_score(labels, predictions, average=average_type, zero_division=0)
        f1 = f1_score(labels, predictions, average=average_type,zero_division=0)

        average_type = 'macro' #macro: each class independently, weighted: giving more weight to classes with more samples

        precision2 = precision_score(labels, predictions, average=average_type, zero_division=0)
        recall2 = recall_score(labels, predictions, average=average_type, zero_division=0)
        f12 = f1_score(labels, predictions, average=average_type,zero_division=0)

        unique, counts = np.unique(predictions, return_counts=True)
        print("Predictions value counts: \n", dict(zip(unique, counts)))
        print(classification_report(labels, predictions))
        #print_conf(predictions, labels)

        return {
            "accuracy": accuracy,
            "precision": precision,
            "recall": recall,
            "f1": f1,
            "precision_macro": precision2,
            "recall_macro": recall2,
            "f1_macro": f12
        }
    except Exception as e:
        print(f"Error computing metrics: {e}")
        return {}

In [ ]:
def load_model():
    model = AutoModelForSequenceClassification.from_pretrained('dbmdz/distilbert-base-turkish-cased', num_labels=49)
    model.resize_token_embeddings(len(tokenizer))
    model.to(device)

    # freeze all the model parameters. (leaves classifier head trainable)
    #for param in model.base_model.parameters():
        #param.requires_grad = False

    trainable_params = [name for name, param in model.named_parameters() if param.requires_grad]
    print("Trainable parameters:", trainable_params)
    print(model.classifier)
    return model

In [ ]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
print(f"Using device: {device}")

Using device: cuda


In [ ]:
from sklearn.model_selection import StratifiedShuffleSplit
import pandas as pd


def stratified_sample(tokenized_split, label_column="label", subset_size=0.1):
    labels = tokenized_split[label_column]
    df = pd.DataFrame({"label": labels})

    splitter = StratifiedShuffleSplit(n_splits=1, test_size=subset_size, random_state=42)
    for _, subset_idx in splitter.split(df, df["label"]):
        subset_tokenized_split = tokenized_split.select(subset_idx)

    return subset_tokenized_split


tokenized_ds_subset = {}
for split in ['train', 'test']:
    tokenized_ds_subset[split] = stratified_sample(tokenized_ds[split])

print("Subset size (train):", len(tokenized_ds_subset["train"]))
print("Subset size (test):", len(tokenized_ds_subset["test"]))


Subset size (train): 5183
Subset size (test): 1296


In [ ]:
from torch.utils.data import WeightedRandomSampler
import numpy as np
from transformers import Trainer
from torch.utils.data import DataLoader, WeightedRandomSampler
import numpy as np
import torch

tokenized_ds["train"] = tokenized_ds["train"].with_format("torch")
class CustomTrainer(Trainer):
    def get_train_dataloader(self):
        if self.train_dataset is None:
            raise ValueError("Trainer: training requires a train_dataset.")

        labels = self.train_dataset['label']
        labels = np.array(labels)

        classes, class_counts = np.unique(labels, return_counts=True)
        class_weights = {cls: 1.0 / count for cls, count in zip(classes, class_counts)}

        sample_weights = np.array([class_weights[label] for label in labels])
        sample_weights = torch.from_numpy(sample_weights).float()

        sampler = WeightedRandomSampler(sample_weights, len(sample_weights), replacement=True)

        # Return a DataLoader with the custom sampler
        return DataLoader(
            self.train_dataset,
            batch_size=self.args.train_batch_size,
            sampler=sampler,
            collate_fn=self.data_collator,
            drop_last=self.args.dataloader_drop_last,
            num_workers=self.args.dataloader_num_workers,
        )

In [14]:
from transformers import TrainingArguments

model=load_model()

training_args=TrainingArguments(
        output_dir="./results",                # Directory where results are saved
        per_device_train_batch_size=32,        # Batch size for training
        per_device_eval_batch_size=32,         # Batch size for evaluation
        num_train_epochs=3,                    # Number of epochs
        evaluation_strategy="epoch",           # Evaluate at the end of each epoch
        logging_strategy="epoch",              # Log at the end of each epoch
        logging_dir='./logs',                  # Log directory
        learning_rate=5e-5,                    # Learning rate
        save_strategy="epoch",                 # Save checkpoints after each epoch                  # Keep only the last checkpoint (optional)
        load_best_model_at_end=False,
)

trainer = CustomTrainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_ds["train"],
    eval_dataset=tokenized_ds["test"],
    tokenizer=tokenizer,
    data_collator=DataCollatorWithPadding(tokenizer=tokenizer),
    compute_metrics=compute_metrics,
)

trainer.train()

trainer.save_model("./results/final_model")

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/410 [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/273M [00:00<?, ?B/s]

Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at dbmdz/distilbert-base-turkish-cased and are newly initialized: ['classifier.bias', 'classifier.weight', 'pre_classifier.bias', 'pre_classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Trainable parameters: ['distilbert.embeddings.word_embeddings.weight', 'distilbert.embeddings.position_embeddings.weight', 'distilbert.embeddings.LayerNorm.weight', 'distilbert.embeddings.LayerNorm.bias', 'distilbert.transformer.layer.0.attention.q_lin.weight', 'distilbert.transformer.layer.0.attention.q_lin.bias', 'distilbert.transformer.layer.0.attention.k_lin.weight', 'distilbert.transformer.layer.0.attention.k_lin.bias', 'distilbert.transformer.layer.0.attention.v_lin.weight', 'distilbert.transformer.layer.0.attention.v_lin.bias', 'distilbert.transformer.layer.0.attention.out_lin.weight', 'distilbert.transformer.layer.0.attention.out_lin.bias', 'distilbert.transformer.layer.0.sa_layer_norm.weight', 'distilbert.transformer.layer.0.sa_layer_norm.bias', 'distilbert.transformer.layer.0.ffn.lin1.weight', 'distilbert.transformer.layer.0.ffn.lin1.bias', 'distilbert.transformer.layer.0.ffn.lin2.weight', 'distilbert.transformer.layer.0.ffn.lin2.bias', 'distilbert.transformer.layer.0.output_

/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


Predictions value counts: 
 {0: 1518, 1: 1032, 2: 512, 3: 1111, 4: 3031, 5: 1367, 6: 3877, 7: 4558, 8: 2001, 9: 974, 10: 493, 11: 1484, 12: 2221, 13: 243, 14: 49, 15: 113, 16: 1714, 17: 7816, 18: 311, 19: 958, 20: 1219, 21: 1839, 22: 4392, 23: 447, 24: 505, 25: 1812, 26: 668, 27: 13574, 28: 245, 29: 1579, 30: 2477, 31: 63, 32: 5170, 33: 10880, 34: 998, 35: 3134, 36: 19449, 37: 105, 38: 1772, 39: 2622, 40: 2312, 41: 6411, 42: 1377, 43: 784, 44: 2751, 45: 887, 46: 1241, 47: 4465, 48: 1001}
              precision    recall  f1-score   support

           0       0.59      0.89      0.71      1005
           1       0.95      0.98      0.97       999
           2       0.90      0.95      0.93       489
           3       0.66      0.91      0.76       797
           4       0.68      0.73      0.71      2843
           5       0.47      0.86      0.61       744
           6       0.93      0.96      0.95      3783
           7       0.82      0.86      0.83      4345
           8       0

Predictions value counts: 
 {0: 1208, 1: 1032, 2: 502, 3: 897, 4: 3494, 5: 1311, 6: 3792, 7: 4539, 8: 1847, 9: 959, 10: 454, 11: 1533, 12: 2177, 13: 230, 14: 26, 15: 105, 16: 1897, 17: 8250, 18: 229, 19: 910, 20: 1241, 21: 1868, 22: 4727, 23: 393, 24: 470, 25: 1739, 26: 650, 27: 14909, 28: 239, 29: 1609, 30: 2496, 31: 54, 32: 5172, 33: 10742, 34: 957, 35: 3139, 36: 19280, 37: 101, 38: 1769, 39: 2298, 40: 2227, 41: 6508, 42: 1293, 43: 530, 44: 2545, 45: 932, 46: 958, 47: 4299, 48: 1025}
              precision    recall  f1-score   support

           0       0.73      0.88      0.80      1005
           1       0.95      0.98      0.97       999
           2       0.93      0.96      0.94       489
           3       0.82      0.92      0.87       797
           4       0.63      0.77      0.69      2843
           5       0.50      0.88      0.64       744
           6       0.96      0.96      0.96      3783
           7       0.83      0.87      0.85      4345
           8       0.7

In [ ]:
# batch size ı düşürürken learning rate i de düşür

In [15]:
trainer.evaluate()

Predictions value counts: 
 {0: 1208, 1: 1032, 2: 502, 3: 897, 4: 3494, 5: 1311, 6: 3792, 7: 4539, 8: 1847, 9: 959, 10: 454, 11: 1533, 12: 2177, 13: 230, 14: 26, 15: 105, 16: 1897, 17: 8250, 18: 229, 19: 910, 20: 1241, 21: 1868, 22: 4727, 23: 393, 24: 470, 25: 1739, 26: 650, 27: 14909, 28: 239, 29: 1609, 30: 2496, 31: 54, 32: 5172, 33: 10742, 34: 957, 35: 3139, 36: 19280, 37: 101, 38: 1769, 39: 2298, 40: 2227, 41: 6508, 42: 1293, 43: 530, 44: 2545, 45: 932, 46: 958, 47: 4299, 48: 1025}
              precision    recall  f1-score   support

           0       0.73      0.88      0.80      1005
           1       0.95      0.98      0.97       999
           2       0.93      0.96      0.94       489
           3       0.82      0.92      0.87       797
           4       0.63      0.77      0.69      2843
           5       0.50      0.88      0.64       744
           6       0.96      0.96      0.96      3783
           7       0.83      0.87      0.85      4345
           8       0.7

{'eval_loss': 0.6720313429832458,
 'eval_accuracy': 0.8212979114246461,
 'eval_precision': 0.8384541279557998,
 'eval_recall': 0.8212979114246461,
 'eval_f1': 0.8222844296776334,
 'eval_precision_macro': 0.7863057416483332,
 'eval_recall_macro': 0.8897262570570721,
 'eval_f1_macro': 0.8304526572307745,
 'eval_runtime': 524.0234,
 'eval_samples_per_second': 247.245,
 'eval_steps_per_second': 7.727,
 'epoch': 3.0}

In [18]:
trainer.evaluate(eval_dataset=tokenized_ds["eval"])

Predictions value counts: 
 {0: 616, 1: 518, 2: 255, 3: 478, 4: 1707, 5: 653, 6: 1900, 7: 2278, 8: 875, 9: 480, 10: 231, 11: 768, 12: 1083, 13: 109, 14: 10, 15: 47, 16: 947, 17: 4105, 18: 113, 19: 441, 20: 631, 21: 942, 22: 2388, 23: 191, 24: 234, 25: 888, 26: 328, 27: 7386, 28: 121, 29: 793, 30: 1273, 31: 22, 32: 2599, 33: 5386, 34: 482, 35: 1569, 36: 9673, 37: 49, 38: 843, 39: 1155, 40: 1128, 41: 3244, 42: 648, 43: 278, 44: 1263, 45: 472, 46: 469, 47: 2206, 48: 506}
              precision    recall  f1-score   support

           0       0.74      0.91      0.81       502
           1       0.94      0.98      0.96       500
           2       0.92      0.96      0.94       245
           3       0.79      0.95      0.86       398
           4       0.65      0.78      0.71      1422
           5       0.51      0.90      0.65       372
           6       0.95      0.96      0.95      1892
           7       0.84      0.88      0.86      2173
           8       0.81      0.86      0

{'eval_loss': 0.6638721823692322,
 'eval_accuracy': 0.822772109106065,
 'eval_precision': 0.8395966494602148,
 'eval_recall': 0.822772109106065,
 'eval_f1': 0.823510908625391,
 'eval_precision_macro': 0.7958464460663418,
 'eval_recall_macro': 0.891703243633816,
 'eval_f1_macro': 0.8361304352331568,
 'eval_runtime': 262.3403,
 'eval_samples_per_second': 246.935,
 'eval_steps_per_second': 7.719,
 'epoch': 3.0}

In [ ]:
!pip install peft

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 320.7/320.7 kB 4.8 MB/s eta 0:00:00


In [ ]:
from peft import LoraConfig, get_peft_model, TaskType
from transformers import AutoModelForCausalLM

config = LoraConfig(
    r=16,
    lora_alpha=32,
    lora_dropout=0.05,
    task_type=TaskType.SEQ_CLS,
    inference_mode=False,
    target_modules= ['q_lin', 'v_lin', 'k_lin', 'out_lin'], #attention mechanism, Q-V emphasizing certain keywords are critical for classification
    #modules_to_save=["classifier"], #also train classifier
)

# PEFT model
lora_model = get_peft_model(model, config)

lora_model.print_trainable_parameters()

for name, param in lora_model.named_parameters():
    if 'lora' not in name:
        param.requires_grad = False

for name, param in lora_model.named_parameters():
    if param.requires_grad:
        print(name, param.shape)

trainer = Trainer(
    model=lora_model,
    args=TrainingArguments(
        output_dir="./lora/results",
        learning_rate=2e-5,
        # Set the per device train batch size and eval batch size
        per_device_train_batch_size=4,
        per_device_eval_batch_size=4,
        # Evaluate and save the model after each epoch
        eval_strategy="epoch",
        save_strategy="epoch",
        num_train_epochs=2,
        weight_decay=0.01,
        logging_dir='./logs',
        logging_steps=10,
        remove_unused_columns=False, #trainer does drop all the dataset columns that are not actual input to the models for training
    ),
    train_dataset=tokenized_ds["train"],
    eval_dataset=tokenized_ds["test"],
    tokenizer=tokenizer,
    data_collator=DataCollatorWithPadding(tokenizer=tokenizer),
    compute_metrics=compute_metrics,
)


trainer.train()
#lora_model.save_pretrained("gpt-lora") # only saves the adapter weights and not the weights of the original model

trainable params: 1,218,097 || all params: 69,344,354 || trainable%: 1.7566
base_model.model.distilbert.transformer.layer.0.attention.q_lin.lora_A.default.weight torch.Size([16, 768])
base_model.model.distilbert.transformer.layer.0.attention.q_lin.lora_B.default.weight torch.Size([768, 16])
base_model.model.distilbert.transformer.layer.0.attention.k_lin.lora_A.default.weight torch.Size([16, 768])
base_model.model.distilbert.transformer.layer.0.attention.k_lin.lora_B.default.weight torch.Size([768, 16])
base_model.model.distilbert.transformer.layer.0.attention.v_lin.lora_A.default.weight torch.Size([16, 768])
base_model.model.distilbert.transformer.layer.0.attention.v_lin.lora_B.default.weight torch.Size([768, 16])
base_model.model.distilbert.transformer.layer.0.attention.out_lin.lora_A.default.weight torch.Size([16, 768])
base_model.model.distilbert.transformer.layer.0.attention.out_lin.lora_B.default.weight torch.Size([768, 16])
base_model.model.distilbert.transformer.layer.1.attentio

KeyboardInterrupt: 

In [ ]:
trainer.evaluate()

{'eval_loss': 2.8777806758880615,
 'eval_accuracy': 0.256875,
 'eval_precision': 0.0959122252978867,
 'eval_recall': 0.256875,
 'eval_f1': 0.13175986402861384,
 'eval_precision_macro': 0.015981550696942445,
 'eval_recall_macro': 0.03112788434393712,
 'eval_f1_macro': 0.01666490016515341,
 'eval_runtime': 8.3941,
 'eval_samples_per_second': 190.61,
 'eval_steps_per_second': 47.652,
 'epoch': 2.0}

In [ ]:
model_save_path = "./trained_model"
model.save_pretrained(model_save_path)

In [ ]:
!zip -r trained_model.zip ./trained_model

In [ ]:
from google.colab import files
files.download("trained_model.zip")